<h1>Imports</h1>

In [16]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from datetime import date
from plotly.subplots import make_subplots

<H1>Pre-Processing</h1>

In [17]:
excel_data = "quant_data.xlsx"
cost = pd.read_excel(excel_data,sheet_name=1)
values = pd.read_excel(excel_data,sheet_name=2)
demographics = pd.read_excel(excel_data,sheet_name=3)

In [18]:
#Add total monthly costs to dataframe
cost['Month'] = pd.to_datetime(cost['Month'])
cost['Total'] = cost.sum(axis=1)
cost

Month  Paid Search  Affiliates      Total
0 2013-01-01     41512.00       16421   57933.00
1 2013-02-01     61243.00       42101  103344.00
2 2013-03-01     84597.88      141321  225918.88

In [86]:
demographics['Registration Date'] = pd.to_datetime(demographics['Registration Date'])
demographics = demographics.sort_values(by='Registration Date')
demographics

jan_signups = demographics[demographics['Registration Date'].dt.strftime('%Y-%m') == '2013-01']
feb_signups = demographics[demographics['Registration Date'].dt.strftime('%Y-%m') == '2013-02']
mar_signups = demographics[demographics['Registration Date'].dt.strftime('%Y-%m') == '2013-03']

In [20]:
today = pd.to_datetime("today")
demographics['Age'] = today.year - demographics['Date Of Birth'].dt.year
#  - (today.month < demographics['Date Of Birth'].dt.month and today.day < demographics['Date Of Birth'].dt.day)
demographics

Customer ID Title Date Of Birth Address City Contact Allowed  \
0                1    Mr    1973-06-29     Malahide               Y   
1                2    Mr    1984-07-25       Dublin               Y   
2                3    Mr    1991-05-01       Dublin               Y   
3                4    Mr    1986-11-30       Dublin               N   
4                5    Mr    1991-10-02     Limerick               Y   
...            ...   ...           ...          ...             ...   
24079        24080    Mr    1971-04-13       Dublin               Y   
24080        24081    Mr    1973-08-27       Dublin               Y   
24081        24082    Mr    1980-08-26       Dublin               N   
24082        24083    Mr    1959-03-18      Ballina               N   
24083        24084  Miss    1975-03-12      Clonmel               Y   

        Registration Date Source of Customer  Age  
0     2013-01-01 00:23:00     Organic Search   49  
1     2013-01-01 00:30:00         Affiliates   38  
2     2013-01-01 01:09:00        Paid Social   31  
3     2013-01-01 01:19:00         Affiliates   36  
4     2013-01-01 01:58:00        Paid Search   31  
...                   ...                ...  ...  
24079 2013-03-31 23:07:00         Affiliates   51  
24080 2013-03-31 23:16:00     Organic Search   49  
24081 2013-03-31 23:32:00     Organic Search   42  
24082 2013-03-31 23:39:00     Organic Search   63  
24083 2013-03-31 23:52:00     Organic Search   47  

[31441 rows x 8 columns]

In [21]:
values['Total Profit'] = values['1st Order Profit'] + values['Subsequent Order Profit']
values

Customer ID  1st Order Profit  Subsequent Order Profit  \
0                1           8.97261                 5.307720   
1                2           7.92288                70.156800   
2                3          14.06160                50.803200   
3                4          14.07672                 0.000000   
4                5          22.68000                68.221440   
...            ...               ...                      ...   
30586        31437          11.08800                97.396992   
30587        31438          20.73600                69.672960   
30588        31439           6.89472                41.803776   
30589        31440           8.98800                 0.000000   
30590        31441           2.59200                69.050880   

       Subsequent Orders Count  Total value of all promotions  Total Profit  
0                            1                       6.600000     14.280330  
1                            7                       6.639453     78.079680  
2                            7                       0.000000     64.864800  
3                            0                       0.000000     14.076720  
4                            9                      14.771948     90.901440  
...                        ...                            ...           ...  
30586                        9                      27.623670    108.484992  
30587                       10                       8.870218     90.408960  
30588                        4                       0.000000     48.698496  
30589                        0                       2.519968      8.988000  
30590                        6                       9.196737     71.642880  

[30591 rows x 6 columns]

In [22]:
values['Subsequent Orders Count'].max()

32

<h1>Data Analysis</h1>

<h2> Advertising Costs</h2>

In [89]:
#Price per new user
#price_per_user = cost['Total'].div(total_signups)
# print(total_signups)
# print ("Price per new user:", price_per_user)

0           Customer ID Title Date Of Birth Address...
1           Customer ID Title Date Of Birth Address...
2           Customer ID Title Date Of Birth Address...
dtype: object
Price per new user: 0    1.106584
1    1.577458
2    2.210102
dtype: float64


In [104]:
months = ["January", 'February', 'March']
monthly_signups = [jan_signups, feb_signups, mar_signups]
total_signups = [0,0,0]
ad_invests = make_subplots(subplot_titles = months,
                    rows=1, cols=3,specs=[[{"type": "pie"}, {"type": "pie"},{"type": "pie"}]])

ad_returns = make_subplots(subplot_titles = months,
                    rows=1, cols=3,specs=[[{"type": "pie"}, {"type": "pie"},{"type": "pie"}]])
                                        

for i in range(0,3):
    # Use `hole` to create a donut-like pie chart
    ad_invests.add_trace(
        go.Pie(name = "Money Spent",labels = ['Paid Search', 'Affiliates'],values=[cost['Paid Search'][i],cost['Affiliates'][i]],hole=.3)
        , row=1,col=i+1
    )
    signups = monthly_signups[i]['Source of Customer'].isin(['Paid Search']).sum(axis=0)
    paid_search = signups
    total_signups[i]+=signups


    signups = monthly_signups[i]['Source of Customer'].isin(['Affiliates']).sum(axis=0)
    paid_affiliates = signups
    total_signups[i]+=signups


    ad_returns.add_trace(
        go.Pie(name="Customers Brought In",labels = ['Paid Search', 'Affiliates'],values=[paid_search,paid_affiliates],hole=.3)
        , row=1,col=i+1
    )
    

ad_invests.update_layout(title_text = "Monthly Money Spent")
ad_returns.update_layout(title_text = "Monthly Customers Returned")

ad_invests.show()
ad_returns.show()


price_per_user = cost['Total'].div(total_signups)
ppu = px.bar(labels = ['Month', 'Price'], x=months, y=price_per_user)
ppu.update_layout(title_text = "Price per New User (Lower is better)", xaxis_title = 'Month', yaxis_title = 'Price (€)')
ppu.show()



If paid search brought in as many new users as paid affiliates per euro spent, you would expect ratio of money spent to equal ratio of customers brought in. However, on average paid search accounts for a larger percentage of new users than the percentage of money invested in it. This suggests that money spent on paid search yields greater returns than paid affiliates

In [131]:
sources = px.histogram(demographics['Source of Customer'], histnorm='probability', nbins=30)
sources.update_layout(title = "Breakdown of Customer Sources")
sources.show()

locs = px.histogram(demographics['Address City'], histnorm='probability')
locs.update_layout(title = "Breakdown of Customer Addresses")
locs.show()


According to cso.ie, Dublin accounted for 28.5% of Ireland's population in April 2021, yet 70% of this companies' customers are from Dublin, which means that they are disproportionately represented in the retailers customer base. This may be expected if the retailer focuses on men's business or formal wear due to the metropolitan nature of Dublin, but it is worth further investigation

'Direct' sources are likely returning customers. This suggests significant focus should be directed at retaining users instead of only looking to bring in new users.

<h2>Demographics</h2>

In [26]:
demographics

Customer ID Title Date Of Birth Address City Contact Allowed  \
0                1    Mr    1973-06-29     Malahide               Y   
1                2    Mr    1984-07-25       Dublin               Y   
2                3    Mr    1991-05-01       Dublin               Y   
3                4    Mr    1986-11-30       Dublin               N   
4                5    Mr    1991-10-02     Limerick               Y   
...            ...   ...           ...          ...             ...   
24079        24080    Mr    1971-04-13       Dublin               Y   
24080        24081    Mr    1973-08-27       Dublin               Y   
24081        24082    Mr    1980-08-26       Dublin               N   
24082        24083    Mr    1959-03-18      Ballina               N   
24083        24084  Miss    1975-03-12      Clonmel               Y   

        Registration Date Source of Customer  Age  
0     2013-01-01 00:23:00     Organic Search   49  
1     2013-01-01 00:30:00         Affiliates   38  
2     2013-01-01 01:09:00        Paid Social   31  
3     2013-01-01 01:19:00         Affiliates   36  
4     2013-01-01 01:58:00        Paid Search   31  
...                   ...                ...  ...  
24079 2013-03-31 23:07:00         Affiliates   51  
24080 2013-03-31 23:16:00     Organic Search   49  
24081 2013-03-31 23:32:00     Organic Search   42  
24082 2013-03-31 23:39:00     Organic Search   63  
24083 2013-03-31 23:52:00     Organic Search   47  

[31441 rows x 8 columns]

In [118]:
age_hist = px.histogram(x=demographics["Age"], histnorm='probability', nbins=30)
age_hist.update_layout(title = "Breakdown of Customer Ages", xaxis_title="Age", yaxis_title="Probability (%)")
age_hist.show()

30-50 age range acount for 75% of customers

In [28]:
cost['Paid Search']

0    41512.00
1    61243.00
2    84597.88
Name: Paid Search, dtype: float64

<h2> Profits </h>

In [29]:
# values = values.sort_values(by=['Total Profit'], ascending = False)
values = values.sort_values(by=['Customer ID'])
values


Customer ID  1st Order Profit  Subsequent Order Profit  \
0                1           8.97261                 5.307720   
1                2           7.92288                70.156800   
2                3          14.06160                50.803200   
3                4          14.07672                 0.000000   
4                5          22.68000                68.221440   
...            ...               ...                      ...   
30586        31437          11.08800                97.396992   
30587        31438          20.73600                69.672960   
30588        31439           6.89472                41.803776   
30589        31440           8.98800                 0.000000   
30590        31441           2.59200                69.050880   

       Subsequent Orders Count  Total value of all promotions  Total Profit  
0                            1                       6.600000     14.280330  
1                            7                       6.639453     78.079680  
2                            7                       0.000000     64.864800  
3                            0                       0.000000     14.076720  
4                            9                      14.771948     90.901440  
...                        ...                            ...           ...  
30586                        9                      27.623670    108.484992  
30587                       10                       8.870218     90.408960  
30588                        4                       0.000000     48.698496  
30589                        0                       2.519968      8.988000  
30590                        6                       9.196737     71.642880  

[30591 rows x 6 columns]

In [30]:
 
fig = px.histogram(values,x='Total Profit',color="Subsequent Orders Count", nbins=30)
fig.update_layout(title = "Breakdown of Profit from Customers", xaxis_title="Profit (€)", yaxis_title="Count")
fig.show()

In [141]:
orders_hist = px.histogram(values['Subsequent Orders Count'], histnorm='probability')
orders_hist.update_layout(title = "Breakdown of Subsequent Orders")
orders_hist.show()

In [32]:
demographics

Customer ID Title Date Of Birth Address City Contact Allowed  \
0                1    Mr    1973-06-29     Malahide               Y   
1                2    Mr    1984-07-25       Dublin               Y   
2                3    Mr    1991-05-01       Dublin               Y   
3                4    Mr    1986-11-30       Dublin               N   
4                5    Mr    1991-10-02     Limerick               Y   
...            ...   ...           ...          ...             ...   
24079        24080    Mr    1971-04-13       Dublin               Y   
24080        24081    Mr    1973-08-27       Dublin               Y   
24081        24082    Mr    1980-08-26       Dublin               N   
24082        24083    Mr    1959-03-18      Ballina               N   
24083        24084  Miss    1975-03-12      Clonmel               Y   

        Registration Date Source of Customer  Age  
0     2013-01-01 00:23:00     Organic Search   49  
1     2013-01-01 00:30:00         Affiliates   38  
2     2013-01-01 01:09:00        Paid Social   31  
3     2013-01-01 01:19:00         Affiliates   36  
4     2013-01-01 01:58:00        Paid Search   31  
...                   ...                ...  ...  
24079 2013-03-31 23:07:00         Affiliates   51  
24080 2013-03-31 23:16:00     Organic Search   49  
24081 2013-03-31 23:32:00     Organic Search   42  
24082 2013-03-31 23:39:00     Organic Search   63  
24083 2013-03-31 23:52:00     Organic Search   47  

[31441 rows x 8 columns]

In [34]:
import dash
import dash_table
import dash_core_components as dcc
import dash_html_components as html
from dash.dependencies import Input, Output
import dash_bootstrap_components as dbc

In [43]:
app = dash.Dash()

In [155]:
# create a Dash layout
app = dash.Dash(external_stylesheets=[dbc.themes.BOOTSTRAP])
app.layout = dbc.Container(dbc.Jumbotron(
    [
        html.H1("Time Series Analysis on Stocks Prediction", className="display-3"),
        html.P(
            "Group 40 ",
            className="lead",
        ),
        html.Hr(className="my-2"),
    
        dbc.Card(
             [
                 dbc.CardBody(
                    [
                        html.H2("Introduction", className="intro-card"),
                        html.P(
                            "sd"
                            ,
                            className="intro-text",
                            ),
                    ],
                    style={"width":"100%"},
                    )
                 ]
            ),
        
        dbc.Card(
             [
                 dbc.CardBody(
                    [
                        html.H2("Marketing", className="normalization-card"),
                        html.H3("Budgeting Paid Search vs. Affiliates"),
                        html.P(
                        "The two rows of pie charts below visualises the monthly proportion of money invested into "
                        "Paid Search vs. Paid Affiliates, and the monthly proportion of customers gained by "
                        "Paid Search vs. Paid Affiliates."),
                        dcc.Graph(figure=ad_invests),
                        dcc.Graph(figure=ad_returns),
                        html.P([
                            "From these visualisations we see that on average, Paid Search accounts for a greater "
                            "proportion of new customers than the proportion of money invested in it. "
                            "This suggests that Paid Search provides greater returns on investment than Paid Affiliate, "
                            "and should be prioritised as such in the marketing budget. "
                            ,html.Br(), "    For another visualisation of "
                            "this relationship, see the below bar chart. It shows the monthly price per customer, "
                            "which is the money spent in advertising divided by the number of customers gained. The price per customer "
                            "increases as the proportion of money spent on Affiliates increases which shows that it "
                            "offers worse returns than money invested into Paid Search."
                        ]),
                        dcc.Graph(figure=ppu),
                        html.P("Note that no information is given about Paid Social, so it is hard to comment on how "
                               "valuable investment in it is, which will shape the overall budgeting of paid advertising."),
                        html.H3("Customer Sources"),
                        dcc.Graph(figure=sources),
                        html.P("The above bar chart shows how many customers were brought to the "
                               "retailers site by each marketing source over the given three months.")

                    ],
                    style={"width":"100%"},
                    )
                 ]
            ),
        
        dbc.Card(
             [
                 dbc.CardBody(
                    [
                    html.H2("Customer Demographics"),
                    html.H3("    Age"),
                    dcc.Graph(figure=age_hist),
                    html.P(
                        "The above histogram shows the distribution of the customer's ages. 24% of customers are "
                        "35-39, and around 63% of the retailer's customers are aged 30-44. Customers aged 20-25 "
                        "account for only 0.05% of the retailer's customer base. Unless the clients specialises in "
                        "fashion for older men, it is likely that the retailer is failing in its marketing "
                        "efforts to reach a younger audience. Exploring new approaches should be a high priority "
                        "for the retailer."
                    ),
                        
                html.H3("    Location"),
                    dcc.Graph(figure=locs),
                html.P(
                    "As seen above, 70% of customers are located in Dublin. However, according to "
                     "cso.ie, Dublin accounted for only 28.5% of Ireland's population in April 2021. This suggests that "
                    "there is a large untapped pool of customers in other regions of the country who aren't "
                    "being reached by the current marketing efforts."
                    ,
                    className="d-text",
                )
                 ]
            ),
        
        dbc.Card(
             [
                 dbc.CardBody(
                    [
                        html.H2("Customer Retention"),
                        dcc.Graph(figure=orders_hist),
                html.P(
                    "The above histogram shows how many additional orders a customer makes with the retailer "
                    "after their first purchase. 35% of customers have never returned to make another order, "
                    "Discounts and sales can entice customers into returning, and additional research should "
                    "be done to determine the execution of these sales can be improved, whether by making the "
                    "sales more significant and thus more attractive, or whether marketing about these sales are "
                    "not reaching the intended audience.",
                    className="intro-text",
                            ),
                 ]
            ),

        dbc.Card(
        [
                 dbc.CardBody(
                [
                        html.H2("Conclusion"),
                html.P(
                    "3 months of data is a small sample size to draw conclusions from, but it "
                    " suggests that there are a number of potential improvements "
                    "that the retailer can make in their marketing efforts which could boost their commercial success."
                    "significantly. Primarily, the retailer seems to "
                ),

                 ]
                ),
            
        ]
        )
             ]
        )
             ]
        )
    ]
)
                          
)


In [ ]:
#run server
app.run_server()

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is run

 * Running on http://127.0.0.1:8050/ (Press CTRL+C to quit)
127.0.0.1 - - [07/Mar/2022 20:54:43] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [07/Mar/2022 20:54:43] "GET /assets/diagnostics.png HTTP/1.1" 404 -
127.0.0.1 - - [07/Mar/2022 20:54:43] "GET /_dash-component-suites/dash_bootstrap_components/_components/dash_bootstrap_components.v0_12_0m1618231905.min.js HTTP/1.1" 200 -
127.0.0.1 - - [07/Mar/2022 20:54:43] "GET /_dash-dependencies HTTP/1.1" 200 -
127.0.0.1 - - [07/Mar/2022 20:54:43] "GET /_dash-layout HTTP/1.1" 200 -
